In [ ]:
%load_ext autoreload
%autoreload 2

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
import os
import sys
from pathlib import Path

workding_dir = str(Path.cwd().parent)
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /home/inflaton/code/projects/courses/llm-finetuning


In [ ]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /home/inflaton/code/projects/courses/llm-finetuning/.env


True

In [ ]:
import os

model_name = os.getenv("MODEL_NAME")
token = os.getenv("HF_TOKEN") or None
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
local_model = os.getenv("LOCAL_MODEL")
hub_model = os.getenv("HUB_MODEL")
num_train_epochs = int(os.getenv("NUM_TRAIN_EPOCHS") or 0)
data_path = os.getenv("DATA_PATH")
results_path = os.getenv("RESULTS_PATH")

max_seq_length = 2048  # Choose any! We auto support RoPE Scaling internally!
dtype = (
    None  # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
)

model_name, load_in_4bit, local_model, hub_model, max_seq_length, num_train_epochs, dtype, data_path, results_path

('unsloth/Qwen2-0.5B-Instruct-bnb-4bit',
 True,
 None,
 None,
 2048,
 10,
 None,
 'datasets/mac/mac.tsv',
 'results/mac-results_lf.csv')

In [ ]:
!nvidia-smi

Sat Jun 29 17:26:00 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 545.23.07              Driver Version: 546.12       CUDA Version: 12.3     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA GeForce RTX 4080 ...    On  | 00000000:01:00.0 Off |                  N/A |
| N/A   50C    P8               4W / 150W |    129MiB / 12282MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [ ]:
from llm_toolkit.translation_engine import load_translation_dataset

dataset = load_translation_dataset(data_path)

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.


[nltk_data] Downloading package wordnet to /home/inflaton/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to /home/inflaton/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /home/inflaton/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


loading /home/inflaton/code/projects/courses/llm-finetuning/llm_toolkit/translation_engine.py
loading train/test data files


Generating train split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['chinese', 'english'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english'],
        num_rows: 1133
    })
})


In [ ]:
df = dataset["train"].to_pandas()

In [ ]:
import pandas as pd

df_alpaca = pd.DataFrame({"instruction": ["Please translate the following Chinese text into English and provide only the translated content, nothing else."]*len(df)})

In [ ]:
df_alpaca["input"] = df["chinese"]
df_alpaca["output"] = df["english"]
df_alpaca

instruction  \
0     Please translate the following Chinese text in...   
1     Please translate the following Chinese text in...   
2     Please translate the following Chinese text in...   
3     Please translate the following Chinese text in...   
4     Please translate the following Chinese text in...   
...                                                 ...   
4523  Please translate the following Chinese text in...   
4524  Please translate the following Chinese text in...   
4525  Please translate the following Chinese text in...   
4526  Please translate the following Chinese text in...   
4527  Please translate the following Chinese text in...   

                                                  input  \
0                                              全仗着狐仙搭救。   
1         过后，表哥告诉她俩，这人是导演，在外国留过学的，还会编剧，今天拍的这戏，就是他自编自导的。   
2                             这凤姐忽然想起一件事来，便向窗外叫：“蓉儿回来！”   
3     三个老红卫兵走到叶文洁面前，面对着她站成了一排——当年，她们也是这样面对叶哲泰的——试图再现...   
4                         程先生照单全收，都是一个“谢”字，然后问王琦瑶有什么话说。   
...                                                 ...   
4523                      外边有两张腿歪面裂的八仙桌子，桌旁胡乱搡着几条狭窄的木凳。   
4524                                       贾瑞听了，喜的抓耳挠腮。   
4525                     听了这样的评价，我们心情激动，和大家一起振臂高呼：打倒王二！   
4526                                       海老公道：“记住了吗？”   
4527                                       上面说，这样写缺少细节。   

                                                 output  
0               Because I was protected by a fox fairy.  
1     He was the director, the cousin later told the...  
2     Xi-feng suddenly seemed to remember something,...  
3     The three old Red Guards stood in front of Ye ...  
4     Mr. Cheng accepted their toast with equanimity...  
...                                                 ...  
4523  Two rickety tables with scarred tops and a few...  
4524  At this last remark Jia Rui positively scratch...  
4525  Hearing comments like this, our emotions were ...  
4526                           'Can you remember that?'  
4527  This time the opinions from above said it need...  

[4528 rows x 3 columns]

In [ ]:
df_alpaca.to_json(
    "llama-factory/data/alpaca_mac.json", orient="records", lines=False, indent=2
)

In [ ]:
df = pd.read_json("llama-factory/data/alpaca_mac.json", orient="records", lines=False)

In [ ]:
df.head()

instruction  \
0  Please translate the following Chinese text in...   
1  Please translate the following Chinese text in...   
2  Please translate the following Chinese text in...   
3  Please translate the following Chinese text in...   
4  Please translate the following Chinese text in...   

                                               input  \
0                                           全仗着狐仙搭救。   
1      过后，表哥告诉她俩，这人是导演，在外国留过学的，还会编剧，今天拍的这戏，就是他自编自导的。   
2                          这凤姐忽然想起一件事来，便向窗外叫：“蓉儿回来！”   
3  三个老红卫兵走到叶文洁面前，面对着她站成了一排——当年，她们也是这样面对叶哲泰的——试图再现...   
4                      程先生照单全收，都是一个“谢”字，然后问王琦瑶有什么话说。   

                                              output  
0            Because I was protected by a fox fairy.  
1  He was the director, the cousin later told the...  
2  Xi-feng suddenly seemed to remember something,...  
3  The three old Red Guards stood in front of Ye ...  
4  Mr. Cheng accepted their toast with equanimity...

In [ ]:
%%time
!python --version
!pip show flash-attn

Python 3.11.9
CPU times: user 23.2 ms, sys: 3.38 ms, total: 26.6 ms
Wall time: 518 ms


In [ ]:
%%time

!./scripts/tune-lf.sh config/qwen2_0.5b_lora_sft.yaml

Current Directory:
/home/inflaton/code/projects/courses/llm-finetuning/llama-factory
06/29/2024 21:58:18 - INFO - llamafactory.hparams.parser - Process rank: 0, device: cuda:0, n_gpu: 1, distributed training: False, compute dtype: torch.bfloat16
[INFO|tokenization_utils_base.py:2161] 2024-06-29 21:58:18,444 >> loading file vocab.json from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-0.5B-Instruct/snapshots/c291d6fce4804a1d39305f388dd32897d1f7acc4/vocab.json
[INFO|tokenization_utils_base.py:2161] 2024-06-29 21:58:18,444 >> loading file merges.txt from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-0.5B-Instruct/snapshots/c291d6fce4804a1d39305f388dd32897d1f7acc4/merges.txt
[INFO|tokenization_utils_base.py:2161] 2024-06-29 21:58:18,444 >> loading file tokenizer.json from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-0.5B-Instruct/snapshots/c291d6fce4804a1d39305f388dd32897d1f7acc4/tokenizer.json
[INFO|tokenization_utils_base.py

In [ ]:
%%time

!./scripts/tune-lf.sh config/qwen2_1.5b_lora_sft.yaml

Current Directory:
/home/inflaton/code/projects/courses/llm-finetuning/llama-factory
06/30/2024 06:14:31 - INFO - llamafactory.hparams.parser - Process rank: 0, device: cuda:0, n_gpu: 1, distributed training: False, compute dtype: torch.bfloat16
[INFO|tokenization_utils_base.py:2161] 2024-06-30 06:14:31,888 >> loading file vocab.json from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-1.5B-Instruct/snapshots/ba1cf1846d7df0a0591d6c00649f57e798519da8/vocab.json
[INFO|tokenization_utils_base.py:2161] 2024-06-30 06:14:31,888 >> loading file merges.txt from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-1.5B-Instruct/snapshots/ba1cf1846d7df0a0591d6c00649f57e798519da8/merges.txt
[INFO|tokenization_utils_base.py:2161] 2024-06-30 06:14:31,888 >> loading file tokenizer.json from cache at /home/inflaton/.cache/huggingface/hub/models--Qwen--Qwen2-1.5B-Instruct/snapshots/ba1cf1846d7df0a0591d6c00649f57e798519da8/tokenizer.json
[INFO|tokenization_utils_base.py

In [ ]:
%%time

!./scripts/tune-lf.sh config/qwen2_7b_lora_sft.yaml